## Imports

In [1]:
import pyxdf 
import numpy as np
import pandas as pd
from lmfit.models import Model
from scipy.spatial.transform import Rotation as R
from scipy import stats
import pywt
import math
import plotly.express as px
import plotly.graph_objects as go
from pandas.api.types import CategoricalDtype

## Function Definitions

Predicted pupil dilation, $d(Y)$, caused by luminance $Y$, is computed with the following equation: $𝑑(𝑌) = 𝑎 · 𝑒^{−𝑏·𝑌} + c$

In [2]:
def pupil_func(x, a, b, c):
    return a * np.exp(-b * x) + c

In [3]:
def modmax(d):
    # compute signal modulus
    m = [0.0]*len(d)
    for i in range(len(d)):
        m[i] = math.fabs(d[i])
    # if value is larger than both neighbours , and strictly larger than either , then it is a local maximum
    t = [0.0]*len(d)
    for i in range(len(d)):
        ll = m[i -1] if i >= 1 else m[i]
        oo = m[i]
        rr = m[i+1] if i < len(d)-2 else m[i]
        if (ll <= oo and oo >= rr) and (ll < oo or oo > rr):
        # compute magnitude
            t[i] = math.sqrt(d[i]**2)
        else:
            t[i] = 0.0
    return t

In [4]:
def ipa_func(d):
    # obtain 2-level DWT of pupil diameter signal d
    try:
        (cA2 ,cD2 ,cD1) = pywt.wavedec(d,'sym16', 'per', level=2)
    except ValueError :
        return
    # get signal duration (in seconds)
    tt = d.index[-1] - d.index[0]
    # normalize by 1/2 j , j = 2 for 2-level DWT
    cA2 [:] = [x / math.sqrt (4.0) for x in cA2]
    cD1 [:] = [x / math.sqrt (2.0) for x in cD1]
    cD2 [:] = [x / math.sqrt (4.0) for x in cD2]

    # detect modulus maxima , see Listing 2
    cD2m = modmax(cD2)
    # threshold using universal threshold λuniv = σˆp(2logn)
    # where σˆ is the standard deviation of the noise
    λuniv = np.std(cD2m) * math.sqrt (2.0* np.log2(len(cD2m )))
    cD2t = pywt. threshold (cD2m ,λuniv,mode="hard")
    # compute IPA
    ctr = 0
    for i in range(len(cD2t )):
        if math.fabs(cD2t[i]) > 0: ctr += 1
    IPA = float(ctr)/tt.total_seconds()

    return IPA

In [5]:
def import_data(file):
    streams, header = pyxdf.load_xdf(file)
    dfs = {}
    for stream in streams:
        stream_name = stream['info']['name'][0]
        stream_channels = {channel['label'][0]: i for i, channel in enumerate(stream['info']['desc'][0]['channels'][0]['channel'])}
        stream_data = stream['time_series']
        data_dict = {key: np.array(stream_data)[:, index] for key, index in stream_channels.items()}
        data_dict['time'] = np.round(np.array(stream['time_stamps']), decimals=4)
        dfs[stream_name] = pd.DataFrame(data_dict).drop_duplicates(subset=['time']).reset_index(drop=True)
    return dfs

In [6]:
accom_time = pd.to_timedelta(0.5, unit='s')

In [7]:
def process_gaze_luminance_data(stream_df):
    pupil = stream_df['GazeStream'].loc[(stream_df['GazeStream']['LeftEyeIsBlinking'] == 0) 
                                        & (stream_df['GazeStream']['RightEyeIsBlinking'] == 0) 
                                        & (stream_df['GazeStream']['LeftPupilDiameter'] > 0) 
                                        & (stream_df['GazeStream']['RightPupilDiameter'] > 0), 
                                        ['time', 'MethodID', 'ModelID', 'LeftPupilDiameter', 'RightPupilDiameter']]
    pupil['time'] = pd.to_timedelta(pupil['time'], unit='s')

    lum = stream_df['LuminanceStream'].loc[:, ['time', 'MethodID', 'ModelID', 'Luminance']]
    lum['time'] = pd.to_timedelta(lum['time'], unit='s')

    # Intersection of time stamps
    pupil_lum_time_intersection = np.intersect1d(pupil['time'], lum['time'])

    # Filter pupil and luminance data by intersection
    pupil = pupil[pupil['time'].isin(pupil_lum_time_intersection)].reset_index(drop=True)
    lum = lum[lum['time'].isin(pupil_lum_time_intersection)].reset_index(drop=True)

    # Combined DataFrame for pupil and luminance
    pupil_lum = pd.DataFrame({
        'time': pd.to_timedelta(pupil_lum_time_intersection, unit='s'),
        'luminance': lum['Luminance'],
        'pupilDiameter': 0.5 * (pupil['LeftPupilDiameter'] + pupil['RightPupilDiameter']),
        'methodID': pupil['MethodID'],
        'modelID': pupil['ModelID']
    })

    return pupil_lum

In [8]:
def process_calibration_data(pupil_lum_df, stream_df):
    calibration_events = stream_df['ExperimentStream'].loc[(stream_df['ExperimentStream']['EventType'] == 'CalibrationColorChange') | 
                                                           (stream_df['ExperimentStream']['SceneEvent'] == 'Calibration') | 
                                                           (stream_df['ExperimentStream']['SceneEvent'] == 'CalibrationComplete'), 
                                                           ['time','SceneEvent', 'EventType']]
    calibration_events['time'] = pd.to_timedelta(calibration_events['time'], unit='s')
    c_start_times = calibration_events[:8]['time']
    c_end_times = calibration_events[1:]['time']
    c_start_times.reset_index(drop=True, inplace=True)
    c_end_times.reset_index(drop=True, inplace=True)

    calib_data = {}
    for i in range(8):
        calib_data[i] = pupil_lum_df.loc[(pupil_lum_df['time'] >= c_start_times[i]) & (pupil_lum_df['time'] <= c_end_times[i]), ['time','luminance', 'pupilDiameter']]
        calib_data[i]['time'] -= calib_data[i]['time'].iloc[0]
        calib_data[i] = calib_data[i].loc[(calib_data[i]['time'] >= accom_time), ['luminance', 'pupilDiameter']]

    calibration_data = pd.concat(calib_data).groupby(level=0).mean().sort_values(by=['luminance']).reset_index(drop=True)
    return calibration_data

In [9]:
def process_navigation_data(pupil_lum_df, stream_df, a, b, c):
    grouped_data = stream_df['NavigationStream'].groupby(['ModelID', 'MethodID'])

    stream_df['SurveyStream']['ModelID'] = stream_df['SurveyStream']['ModelID'].astype(float)
    stream_df['SurveyStream']['MethodID'] = stream_df['SurveyStream']['MethodID'].astype(float)
    
    discomfort_survey = stream_df['SurveyStream'].loc[
        (stream_df['SurveyStream']['SurveyType'] == 'Discomfort') & 
        (stream_df['SurveyStream']['ModelID'] < 4), 
        ['time', 'ModelID', 'MethodID']]
    survey_group = discomfort_survey.groupby(['ModelID', 'MethodID'])

    start_times = []
    end_times = []

    for i in range(4):
        for j in range(2,4):
            trial = grouped_data.get_group((i, j))

            start = trial.loc[(trial['spline_percent'] > 0.001)].index[0]
            start_time = pd.to_timedelta(stream_df['NavigationStream'].loc[start, 'time'], unit='s')

            end = trial.loc[(trial['spline_percent'] > 0.995)]
            end_time = 0
            # For 6DoF navigation, completion was determined by collision with bounding box
            # Spline percentage was based on projection, so it may not reach > 0.995
            # In this case, the survey time serves as the end time
            if len(end) > 0:
                end = end.index[0]
                end_time = pd.to_timedelta(stream_df['NavigationStream'].loc[end, 'time'], unit='s')
            else:
                end = survey_group.get_group((i, j)).index[0]
                end_time = pd.to_timedelta(stream_df['SurveyStream'].loc[end, 'time'], unit='s') - pd.offsets.Second(3)
            
            start_times.append(start_time)
            end_times.append(end_time)


    nav_start_times = start_times
    #nav_start_times.reset_index(drop=True, inplace=True)

    nav_end_times = end_times
    #nav_end_times.reset_index(drop=True, inplace=True)

    nav_data = {}
    for i in range(8):
        nav_data[i] = pupil_lum_df.loc[
            (pupil_lum_df['luminance'] >0) & 
            (pupil_lum_df['time']>nav_start_times[i]) & 
            (pupil_lum_df['time']<nav_end_times[i]), 
            ['time', 'methodID', 'modelID', 'luminance', 'pupilDiameter']]
        nav_data[i].reset_index(drop=True, inplace=True)

    navigation_data = pd.concat(nav_data, names=['trial'])
    navigation_data['pupil_lum_base'] = pupil_func(navigation_data['luminance'], a, b, c)
    navigation_data['adj_pupil'] = navigation_data['pupilDiameter'] - navigation_data['pupil_lum_base']

    return navigation_data

In [10]:
def process_creation_data(pupil_lum_df, stream_df, a, b, c):
    
    crt_start_times = stream_df['CreationStream'].loc[
    (stream_df['CreationStream']['EventName'] == 'StartPointRegistered'), 
    ['time', 'ModelID', 'MethodID']]
    crt_start_times = pd.to_timedelta(crt_start_times.groupby(['ModelID', 'MethodID']).first()['time'], unit='s') + pd.offsets.Second(2)
    crt_start_times.reset_index(drop=True, inplace=True)

    crt_end_times = stream_df['CreationStream'].loc[
    (stream_df['CreationStream']['EventName'] == 'FinishPath'), 
    ['time', 'ModelID', 'MethodID']]
    crt_end_times = pd.to_timedelta(crt_end_times.groupby(['ModelID', 'MethodID']).first()['time'], unit='s')
    crt_end_times.reset_index(drop=True, inplace=True)
    
    crt_data = {}
    for i in range(8):
        crt_data[i] = pupil_lum_df.loc[
            (pupil_lum_df['time'] > crt_start_times.loc[i]) & 
            (pupil_lum_df['time'] < crt_end_times.loc[i]), 
            ['time', 'methodID', 'modelID', 'luminance', 'pupilDiameter']]
        crt_data[i].reset_index(drop=True, inplace=True)

    creation_data = pd.concat(crt_data, names=['trial'])
    creation_data['pupil_lum_base'] = pupil_func(creation_data['luminance'], a, b, c)
    creation_data['adj_pupil'] = creation_data['pupilDiameter'] - creation_data['pupil_lum_base']
    
    return creation_data

In [11]:
def process_creation_stats(stream_df):
    stream_df['CreationStream']['ModelID'] = stream_df['CreationStream']['ModelID'].astype(float)
    stream_df['CreationStream']['MethodID'] = stream_df['CreationStream']['MethodID'].astype(float)
    stream_df['CreationStream']['EventType'] = stream_df['CreationStream']['EventType'].astype("category")

    group = stream_df['CreationStream'].groupby(['ModelID', 'MethodID'])
    creation_counts  = []

    for i in range(4):
            for j in range(0,2):
                trial = group.get_group((i,j))
                creation_counts.append(trial.groupby('EventType', observed=False).size().fillna(0))
    
    keys = [(i,j) for i in range(4) for j in range(0,2)]
    creation_stats = pd.concat(creation_counts, axis=0, keys=keys, names=['ModelID', 'MethodID']).unstack(level=2)
    creation_stats = creation_stats.drop(columns=['End', 'Start'])
    return creation_stats

In [12]:
def process_discomfort_data(stream_df):
    discomfort_values = stream_df['SurveyStream'].loc[stream_df['SurveyStream']['SurveyType'] == 'Discomfort', ['time', 'Value', 'ModelID', 'MethodID']]
    discomfort_values['time'] = pd.to_timedelta(discomfort_values['time'], unit='s')
    discomfort_values.reset_index(drop=True, inplace=True)
    return discomfort_values

In [13]:
def process_seq_data(stream_df):
    seq_values = stream_df['SurveyStream'].loc[stream_df['SurveyStream']['SurveyType'] == 'SEQ', ['time', 'Value', 'ModelID', 'MethodID']]
    seq_values['time'] = pd.to_timedelta(seq_values['time'], unit='s')
    seq_values.reset_index(drop=True, inplace=True)
    return seq_values

In [14]:
def process_ipa_calc(data):
    methods = []
    models = []
    ipa = []
    for i in range(8):
        methods.append(data.loc[i]['methodID'].iloc[i])
        models.append(data.loc[i]['modelID'].iloc[i])
        pupil = data.loc[i]['pupilDiameter']
        pupil.index = data.loc[i]['time']
        ipa.append(ipa_func(pupil))
        
    return pd.DataFrame({'methodID': methods, 'modelID': models, 'IPA': ipa})

## Load Data

Load the data from the xdf file for a single participant.

In [33]:
file = './Path_Data/ID_118.xdf'
df = import_data(file)
df['SurveyStream'] = df['SurveyStream'].replace(r'^\s*$', np.nan, regex=True).dropna()
df['CreationStream'] = df['CreationStream'].replace(r'^\s*$', np.nan, regex=True).dropna()

df['SurveyStream']['ModelID'] = df['SurveyStream']['ModelID'].astype(float)
df['SurveyStream']['MethodID'] = df['SurveyStream']['MethodID'].astype(float)
df['SurveyStream']['Value'] = df['SurveyStream']['Value'].astype(float)

In [34]:
print(df['CreationStream']['EventType'].unique())

['Start' 'PointPlaced' 'Move' 'End' 'Draw' 'Erase']


In [16]:
id = df['ExperimentStream']['UserID'][0]
pupil_lum_df = process_gaze_luminance_data(df)
calibration_data = process_calibration_data(pupil_lum_df, df)

x_data = calibration_data['luminance']
y_data = calibration_data['pupilDiameter']
exp_mod = Model(pupil_func)
params = exp_mod.make_params(a=1, b=4, c=0)
result = exp_mod.fit(y_data, params, x=x_data)
a = result.params['a'].value
b = result.params['b'].value
c = result.params['c'].value

pupil_data = pupil_lum_df.loc[(pupil_lum_df['methodID'] < 5), ['time', 'luminance', 'pupilDiameter']]
pupil_data.reset_index(drop=True, inplace=True)
pupil_data['time'] = pupil_data['time'] - pupil_data['time'][0]
pupil_data['pupil_lum_base'] = pupil_func(pupil_data['luminance'], a, b, c)
pupil_data['adj_pupil'] = pupil_data['pupilDiameter'] - pupil_data['pupil_lum_base']

navigation_data = process_navigation_data(pupil_lum_df, df, a, b, c)

ipa_calc_nav = process_ipa_calc(navigation_data)


In [17]:
creation_stats = process_creation_stats(df)

creation_data = process_creation_data(pupil_lum_df, df, a, b, c)

ipa_calc_crt = process_ipa_calc(creation_data)

discomfort = process_discomfort_data(df)
seq = process_seq_data(df)



method_cats = CategoricalDtype(['4DoF','6DoF', 'unimanual','bimanual'], ordered=False)
model_cats = CategoricalDtype(['A', 'B', 'C', 'D'], ordered=True)

In [18]:
nav_trials = navigation_data.groupby(['modelID', 'methodID'])

nav_data = {}
for i in range(4):
    for j in range(2,4):
        trial = nav_trials.get_group((i, j))
        nav_data[('108',i,j)] = trial.mean()


nav_data = pd.concat(nav_data, axis=1, names=['id', 'modelID', 'methodID']).T
nav_index = pd.MultiIndex.from_product([[id], model_cats.categories, method_cats.categories[0:2]], names=['id', 'modelID', 'methodID'])
nav_data.index = nav_index
nav_data.drop(columns=['time', 'modelID', 'methodID'], inplace=True)

In [19]:
ipa_nav_trials = ipa_calc_nav.groupby(['modelID', 'methodID'])

ipa_nav_data = {}
for i in range(4):
    for j in range(2,4):
        trial = ipa_nav_trials.get_group((i, j))
        ipa_nav_data[('108',i,j)] = trial.mean()


ipa_nav_data = pd.concat(ipa_nav_data, axis=1, names=['id', 'modelID', 'methodID']).T
ipa_nav_data.index = nav_index
ipa_nav_data.drop(columns=['modelID', 'methodID'], inplace=True)

In [20]:
crt_trials = creation_data.groupby(['modelID', 'methodID'])

crt_data = {}
for i in range(4):
    for j in range(0,2):
        trial = crt_trials.get_group((i, j))
        crt_data[('108',i,j)] = trial.mean()

crt_data = pd.concat(crt_data, axis=1, names=['id', 'modelID', 'methodID']).T
crt_index = pd.MultiIndex.from_product([['108'],model_cats.categories, method_cats.categories[2:4]], names=['id', 'modelID', 'methodID'])
crt_data.index = crt_index
crt_data.drop(columns=['time', 'modelID', 'methodID'], inplace=True)

In [21]:
ipa_crt_trials = ipa_calc_crt.groupby(['modelID', 'methodID'])

ipa_crt_data = {}
for i in range(4):
    for j in range(0,2):
        trial = ipa_crt_trials.get_group((i, j))
        ipa_crt_data[('108',i,j)] = trial.mean()

ipa_crt_data = pd.concat(ipa_crt_data, axis=1, names=['id', 'modelID', 'methodID']).T
ipa_crt_data.index = crt_index
ipa_crt_data.drop(columns=['modelID', 'methodID'], inplace=True)

In [22]:
crt_stats = creation_stats
crt_stats.index = crt_index

In [23]:
dis_trials = discomfort.groupby(['ModelID', 'MethodID'])

dis_data = {}
for i in range(4):
    for j in range(2,4):
        trial = dis_trials.get_group((i, j))
        dis_data[('108',i,j)] = trial.mean()

dis_data = pd.concat(dis_data, axis=1, names=['id', 'modelID', 'methodID']).T
dis_data.index = nav_index
dis_data['discomfort'] = dis_data['Value']
dis_data.drop(columns=['time', 'ModelID', 'MethodID', 'Value'], inplace=True)

In [24]:
seq_trials = seq.groupby(['ModelID', 'MethodID'])

seq_data = {}
for i in range(4):
    for j in range(0,4):
        trial = seq_trials.get_group((i, j))
        seq_data[('108',i,j)] = trial.mean()

seq_data = pd.concat(seq_data, axis=1, names=['id', 'modelID', 'methodID']).T
seq_index = dis_index = pd.MultiIndex.from_product([['108'], model_cats.categories, method_cats.categories], names=['id', 'modelID', 'methodID'])
seq_data.index = seq_index
seq_data['seq'] = seq_data['Value']
seq_data.drop(columns=['time', 'ModelID', 'MethodID', 'Value'], inplace=True)

In [25]:
data_df = pd.concat([nav_data, crt_data, ipa_nav_data, ipa_crt_data, dis_data, seq_data, crt_stats], axis=0).stack().unstack()

In [26]:
creation_stats = process_creation_stats(df)

creation_data = process_creation_data(pupil_lum_df, df, a, b, c)

ipa_calc_crt = process_ipa_calc(creation_data)

discomfort = process_discomfort_data(df)
seq = process_seq_data(df)

In [27]:
gaze = df['GazeStream'].loc[
    (df['GazeStream']['LeftEyeIsBlinking'] == 0) & 
    (df['GazeStream']['RightEyeIsBlinking'] == 0) & 
    (df['GazeStream']['ConvergenceDistanceIsValid'] == 1) & 
    (df['GazeStream']['GazeRayIsValid'] == 1), 
    ['time', 'GazeOriginX', 'GazeOriginY', 'GazeOriginZ', 'GazeDirectionNormalizedX', 'GazeDirectionNormalizedY', 'GazeDirectionNormalizedZ']]
gaze['time'] = pd.to_timedelta(gaze['time'], unit='s')

headTransform = df['PoseStream'].loc[:, ['time', 'Head_PosX', 'Head_PosY', 'Head_PosZ', 'Head_RotX', 'Head_RotY', 'Head_RotZ', 'Head_RotW']]
headTransform['time'] = pd.to_timedelta(headTransform['time'], unit='s')

head_pupil_intersection = np.intersect1d(gaze['time'], headTransform['time'])

gaze = gaze[gaze['time'].isin(head_pupil_intersection)].reset_index(drop=True)
headTransform = headTransform[headTransform['time'].isin(head_pupil_intersection)].reset_index(drop=True)

pos_np = headTransform.loc[:, ['Head_PosX', 'Head_PosY', 'Head_PosZ']].to_numpy()
rot_np = headTransform.loc[:, ['Head_RotX', 'Head_RotY', 'Head_RotZ', 'Head_RotW']].to_numpy()
gaze_origin_np = gaze.loc[:, ['GazeOriginX', 'GazeOriginY', 'GazeOriginZ']].to_numpy()
gaze_dir_np = gaze.loc[:, ['GazeDirectionNormalizedX', 'GazeDirectionNormalizedY', 'GazeDirectionNormalizedZ']].to_numpy()

# Construct world to local transformation matrix
local_to_world = np.zeros((4, 4, len(headTransform)))
world_to_local = np.zeros((4, 4, len(headTransform)))
for i in range(len(pos_np)):
    local_to_world[:, :, i] = np.eye(4)
    q = rot_np[i]
    r = R.from_quat(q).as_matrix()
    t = pos_np[i]
    local_to_world[0,0,i] = r[0,0]
    local_to_world[0,1,i] = r[0,1]
    local_to_world[0,2,i] = r[0,2]
    local_to_world[1,0,i] = r[1,0]
    local_to_world[1,1,i] = r[1,1]
    local_to_world[1,2,i] = r[1,2]
    local_to_world[2,0,i] = r[2,0]
    local_to_world[2,1,i] = r[2,1]
    local_to_world[2,2,i] = r[2,2]
    local_to_world[0,3,i] = t[0]
    local_to_world[1,3,i] = t[1]
    local_to_world[2,3,i] = t[2]
    local_to_world[3,3,i] = 1
    world_to_local[:, :, i] = np.linalg.inv(local_to_world[:, :, i])

In [28]:
gaze_origin_local = np.zeros((4, len(gaze_origin_np)))

# Transform gaze origin to local coordinates
for i in range(len(gaze_origin_np)):
    gaze_origin_local[:, i] = np.append(gaze_origin_np[i], 1)
    gaze_origin_local[:, i] = np.matmul(world_to_local[:, :, i], gaze_origin_local[:, i])

gaze_origin_local = gaze_origin_local[:3, :]
df_gaze = pd.DataFrame(gaze_origin_local.T, columns=['GazeOriginX', 'GazeOriginY', 'GazeOriginZ'])
df_gaze.dropna(inplace=True)
print(df_gaze.info())


masked_gaze_origin = np.ma.masked_outside(gaze_origin_local, -0.38, 0.38)
df_masked_gaze = pd.DataFrame(masked_gaze_origin.T, columns=['GazeOriginX', 'GazeOriginY', 'GazeOriginZ'])
df_masked_gaze.dropna(inplace=True)
#find elements in gaze_origin_local that are greater than 1 or less than -1--these are invalied values

print(df_masked_gaze.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 102972 entries, 0 to 102971
Data columns (total 3 columns):
 #   Column       Non-Null Count   Dtype  
---  ------       --------------   -----  
 0   GazeOriginX  102972 non-null  float64
 1   GazeOriginY  102972 non-null  float64
 2   GazeOriginZ  102972 non-null  float64
dtypes: float64(3)
memory usage: 2.4 MB
None
<class 'pandas.core.frame.DataFrame'>
Index: 102787 entries, 0 to 102971
Data columns (total 3 columns):
 #   Column       Non-Null Count   Dtype  
---  ------       --------------   -----  
 0   GazeOriginX  102787 non-null  float64
 1   GazeOriginY  102787 non-null  float64
 2   GazeOriginZ  102787 non-null  float64
dtypes: float64(3)
memory usage: 3.1 MB
None


In [29]:
#plot gaze origin for x, y

fig = go.Figure(data=[go.Scatter(x=df_masked_gaze['GazeOriginX'], y=df_masked_gaze['GazeOriginY'], mode='markers')])
fig.show()